# Columbia University - IEOR 4732: Computational Methods in Finance
# Homework 2 by Alexandre Duhamel - afd2153
<br><br>

### Use explicit-implicit finite difference scheme covered during the lecture to solve the PIDE.

## PIDE Formulation

Let $w(x,\tau)$ be the value of a derivative security that satisfies the following Partial Integro-Differential Equation (PIDE):

$$
\frac{\partial w}{\partial \tau} (x, \tau) - (r - q) \frac{\partial w}{\partial x} (x, \tau) + r w(x, \tau)
- \int_{-\infty}^{\infty} \left[ w(x+y, \tau) - w(x, \tau) - \frac{\partial w}{\partial x} (x, \tau) (e^y - 1) \right] k(y) \, dy = 0.
$$

where

$$
k(y) =
\frac{e^{-\lambda_p y}}{\nu y^{1+Y}} \mathbf{1}_{y>0} +
\frac{e^{-\lambda_n |y|}}{\nu |y|^{1+Y}} \mathbf{1}_{y<0},
$$

with

$$
\lambda_p = \left( \frac{\theta^2}{\sigma^4} + \frac{2}{\sigma^2 \nu} \right)^{\frac{1}{2}} - \frac{\theta}{\sigma^2},
$$

$$
\lambda_n = \left( \frac{\theta^2}{\sigma^4} + \frac{2}{\sigma^2 \nu} \right)^{\frac{1}{2}} + \frac{\theta}{\sigma^2}.
$$

## Initial and Boundary Conditions

The equation is solved with the initial condition:

$$
w(x,0) = (e^x - K)^+,
$$

and the boundary conditions:

$$
w(x_0, \tau) = 0, \quad \forall \tau,
$$

$$
w(x_N, \tau) = w(B, \tau) = 0, \quad \forall \tau.
$$

## Numerical Implementation

### Grid Setup

Define the spatial and time discretization:

$$
x_{\min} = \ln(S_0) - 2, \quad x_{\max} = \ln(B) \text{- delta}, 
$$

Note : we will try different values of delta to test the stability of our model

$$
dx = \frac{x_{\max} - x_{\min}}{N}, \quad dt = \frac{T}{M}.
$$

The discretized spatial and time grids:

$$
x_i = x_{\min} + i \cdot dx, \quad i = 0, 1, \dots, N,
$$

$$
\tau_j = j \cdot dt, \quad j = 0, 1, \dots, M.
$$

### Matrix Form of the PIDE

We initially have such a difference equation:

$$
- B_l w_{i-1,j+1} + (1 + r \Delta \tau + B_l + B_u) w_{i,j+1} + B_u w_{i+1,j+1}
= w_{i,j} + \Delta \tau \int_{|y|>\Delta x} (w(x_i + y, \tau_j) - w_{i,j}) k(y) \, dy.
$$

For $|y|>\Delta x$, we divide it into four sub-intervals and write it as:

$$
\int_{|y|>\Delta x} (w(x_i + y, \tau_j) - w_{i,j}) k(y) \, dy =
\int_{-\infty}^{x_0 - x_i} (w(x_i + y, \tau_j) - w_{i,j}) k(y) \, dy
$$

$$
+ \int_{x_0 - x_i}^{-\Delta x} (w(x_i + y, \tau_j) - w_{i,j}) k(y) \, dy
$$

$$
+ \int_{x_N - x_i}^{+\Delta x} (w(x_i + y, \tau_j) - w_{i,j}) k(y) \, dy
$$

$$
+ \int_{x_N - x_i}^{\infty} (w(x_i + y, \tau_j) - w_{i,j}) k(y) \, dy.
$$

For $y \in (x_0 - x_i, \Delta x)$ the integral:

$$
= \sum_{k=1}^{i-1} \frac{\lambda_n^Y}{\nu} 
\left( w_{i-k,j} - w_{i,j} - k (w_{i-k-1,j} - w_{i-k,j}) \right) 
\Big( g_2(k \lambda_n \Delta x) - g_2((k+1) \lambda_n \Delta x) \Big)
$$

$$
+ \sum_{k=1}^{i-1} \frac{w_{i-k-1,j} - w_{i-k,j}}{\lambda_n^{1-Y} \nu \Delta x}
\Big( g_1(k \lambda_n \Delta x) - g_1((k+1) \lambda_n \Delta x) \Big).
$$

For $y \in (\Delta x, x_N - x_i)$ the integral:

$$
= \sum_{k=1}^{N-i-1} \frac{\lambda_p^Y}{\nu} 
\left( w_{i+k,j} - w_{i,j} - k (w_{i+k+1,j} - w_{i+k,j}) \right) 
\Big( g_2(k \lambda_p \Delta x) - g_2((k+1) \lambda_p \Delta x) \Big)
$$

$$
+ \sum_{k=1}^{N-i-1} \frac{w_{i+k+1,j} - w_{i+k,j}}{\lambda_p^{1-Y} \nu \Delta x}
\Big( g_1(k \lambda_p \Delta x) - g_1((k+1) \lambda_p \Delta x) \Big).
$$

For $y \in (-\infty, x_0 - x_i)$, since $w(x_i-y, \tau_i) = 0$ for a call, the integral:

$$
= -\frac{\lambda_n^Y}{\nu}w_{i,j}g_2(i \lambda_n \Delta x)
$$

For $y \in ((N-i) \Delta x, \infty)$, since $w(x_i+y, \tau_i) = e^{x_i + y} - K$ for a call, the integral:

$$
= -\frac{\lambda_p^Y}{\nu}(K+w_{i,j})g_2((N-i) \lambda_p \Delta x) +
\frac{(\lambda_p+1)^Y}{\nu}e^{x_i}g_2((N-i)(\lambda_p+1) \Delta x)
$$

Using an explicit-implicit finite difference scheme we obtain:

$$
l_{i,j+1} \times w_{i-1,j+1} + d_{i,j+1} \times w_{i,j+1} + u_{i,j+1} \times w_{i+1,j+1} = w_{i,j} +
\frac{\Delta \tau}{\nu} \times R_{i,j}
$$

where

$$
\begin{aligned}
R_{i,j} &= \sum_{k=1}^{i-1} \lambda_n^Y 
\left( w_{i-k,j} - w_{i,j} - k (w_{i-k-1,j} - w_{i-k,j}) \right) 
\Big( g_2(k \Delta x \lambda_n) - g_2((k+1) \Delta x \lambda_n) \Big) \\
&\quad + \sum_{k=1}^{i-1} \frac{w_{i-k-1,j} - w_{i-k,j}}{\lambda_n^{1-Y} \Delta x}
\Big( g_1(k \Delta x \lambda_n) - g_1((k+1) \Delta x \lambda_n) \Big) \\
&\quad + \sum_{k=1}^{N-i-1} \lambda_p^Y 
\left( w_{i+k,j} - w_{i,j} - k (w_{i+k+1,j} - w_{i+k,j}) \right) 
\Big( g_2(k \Delta x \lambda_p) - g_2((k+1) \Delta x \lambda_p) \Big) \\
&\quad + \sum_{k=1}^{N-i-1} \frac{w_{i+k+1,j} - w_{i+k,j}}{\lambda_p^{1-Y} \Delta x}
\Big( g_1(k \Delta x \lambda_p) - g_1((k+1) \Delta x \lambda_p) \Big) \\
&\quad + \cancel{K\lambda_n^Y g_2(i \Delta x \lambda_n)} - \cancel{e^{x_i} (\lambda_n + 1)^Y g_2(i \Delta x (\lambda_n + 1))} \\
&\quad + (\lambda_p-1)^Y e^{x_i} g_2((N-i) (\lambda_p - 1) \Delta x ) - \lambda_p^Y g_2((N-i) \lambda_p \Delta x).
\end{aligned}
$$

The PIDE is discretized in matrix form as:

$$
A W^{j+1} = W^{j} + \frac{\Delta \tau}{\nu} R^{j},
$$

where $W^j$ is the solution vector at time step $j$:

$$
W = \begin{bmatrix}
w(x_0,\tau_0) & w(x_0,\tau_1) & \cdots & w(x_0,\tau_M) \\
w(x_1,\tau_0) & w(x_1,\tau_1) & \cdots & w(x_1,\tau_M) \\
\vdots       & \vdots       & \ddots & \vdots \\
w(x_N,\tau_0) & w(x_N,\tau_1) & \cdots & w(x_N,\tau_M)
\end{bmatrix}.
$$

Each column

$$
W^j = \begin{bmatrix} w(x_0,\tau_j) \\ w(x_1,\tau_j) \\ \vdots \\ w(x_N,\tau_j) \end{bmatrix}
$$

represents the spatial solution at the fixed time level $\tau_j$. In other words, the full matrix $W$ is assembled as

$$
W = \left[ W^0 \; W^1 \; \cdots \; W^M \right],
$$

with each $W^j$ being a vector in space at time $\tau_j$.  

And the matrix $A$ is given by:

$$
A =
\begin{bmatrix}
d_{1,j+1} & u_{1,j+1} & 0 & \dots & 0 & 0 \\
l_{2,j+1} & d_{2,j+1} & u_{2,j+1} & \dots & 0 & 0 \\
0 & l_{3,j+1} & d_{3,j+1} & \dots & 0 & 0 \\
\vdots & \vdots & \vdots & \ddots & \vdots & \vdots \\
0 & 0 & 0 & \dots & d_{N-1,j+1} & u_{N-1,j+1} \\
0 & 0 & 0 & \dots & l_{N,j+1} & d_{N,j+1}
\end{bmatrix}
$$

In the case of $i = 1$ or $i = N - 1$, we impose the boundary conditions.

where:

$$
l_{i,j+1} = -B_l,
$$

$$
d_{i,j+1} = 1 + r \Delta \tau + B_l + B_u + \frac{\Delta \tau}{\nu} 
\left( \lambda_n^Y g_2(i \Delta x \lambda_n) + \lambda_p^Y g_2((N - i) \Delta x \lambda_p) \right),
$$

$$
u_{i,j+1} = -B_u.
$$

### Boundary Coefficients

The coefficients $B_l$ and $B_u$ are given by:

$$
B_l = \frac{\sigma^2 (\Delta x) \Delta \tau}{2\Delta x^2} - \left( r - q + \omega(\Delta x) - \frac{1}{2} \sigma^2 (\Delta x) \right) \frac{\Delta \tau}{2\Delta x},
$$

$$
B_u = \frac{\sigma^2 (\Delta x) \Delta \tau}{2\Delta x^2} + \left( r - q + \omega(\Delta x) - \frac{1}{2} \sigma^2 (\Delta x) \right) \frac{\Delta \tau}{2\Delta x}.
$$

### Integral Functions for the PIDE

Define the functions $g_1(\xi)$ and $g_2(\xi)$ as follows:

$$
g_1(\xi) = \int_{\xi}^{\infty} \frac{e^{-z}}{z^Y} dz,
$$

$$
g_2(\xi) = \int_{\xi}^{\infty} \frac{e^{-z}}{z^{Y+1}} dz.
$$

### Jump Component Integrals

The integral terms for the jump process:

$$
\begin{aligned}
\sigma^2(\epsilon) &= \int_{|y|\leq \epsilon} y^2 k(y) dy \\
&= \frac{1}{\nu} \lambda_p^{Y-2} 
\Big( -(\lambda_p \epsilon)^{1-Y} e^{-\lambda_p \epsilon} 
+ (1-Y) (g_1(0) - g_1(\lambda_p \epsilon)) \Big) \\
&\quad + \frac{1}{\nu} \lambda_n^{Y-2} 
\Big( -(\lambda_n \epsilon)^{1-Y} e^{-\lambda_n \epsilon} 
+ (1-Y) (g_1(0) - g_1(\lambda_n \epsilon)) \Big)
\end{aligned}
$$

$$
\begin{aligned}
\omega(\epsilon) &= \int_{|y|>\epsilon} (1 - e^y) k(y) dy \\
&= \frac{\lambda_p^Y}{\nu} g_2(\lambda_p \epsilon) 
- \frac{(\lambda_p -1)^Y}{\nu} g_2((\lambda_p -1) \epsilon) \\
&\quad + \frac{\lambda_n^Y}{\nu} g_2(\lambda_n \epsilon) 
- \frac{(\lambda_n +1)^Y}{\nu} g_2((\lambda_n +1) \epsilon)
\end{aligned}
$$

These terms account for small and large jumps in the process.

### Numerical Solution Procedure for UOC Call

1. **Initialize the grid** and set the initial condition 
   $$
   w(x,0) = (e^x - K)^+
   $$
   $$
   w(x_0, \tau) = 0 \quad \forall \tau
   $$
   $$
   w(x_N, \tau) = w(B, \tau) = 0 \quad \forall \tau.
   $$

2. **Construct the matrix $A$** using the coefficients $l$, $d$, $u$.

3. **Time-marching loop**:
   - Compute $R_{i,j}$ at each step.
   - Solve the linear system 
     $$
     A W^{j+1} = W^j + \frac{\Delta \tau}{\nu} R^j.
     $$

4. **Extract the option price** at $S_0$.


---

## Let's start the implementation :

In [12]:
import numpy as np
import scipy.linalg as la

In [13]:
# Compute k(y) Lévy-measure function
def k_y(y, lambda_n, lambda_p, nu, Y):
    result = []
    for val in y:
        if val < 0:
            output = np.exp(-lambda_n * np.abs(val)) / (nu * np.abs(val)**(1 + Y))
        elif val > 0:
            output = np.exp(-lambda_p * val) / (nu * val**(1 + Y))
        else:
            output = 0.0
        result.append(output)
    return np.array(result)

# y_values = np.array([-2, -1, -0.5, -0.1, 0.1, 0.5, 1, 2])
# k_values = k_y(y_values, lambda_n, lambda_p, nu, Y)

# print("y values:", y_values)
# print("k(y) values:", k_values)

In [14]:
import scipy.integrate as spi

def g1(xi):
        return spi.quad(lambda z: np.exp(-z) / z**Y, xi, np.inf)[0]
    
def g2(xi):
    return spi.quad(lambda z: np.exp(-z) / z**(Y+1), xi, np.inf)[0]

In [ ]:
# Function to compute B_l and B_u coefficients
def compute_B_coefficients(dx, dt, lambda_n, lambda_p, nu, Y, r, q, pre_computed=True):
    """ Compute B_l and B_u coefficients for the PIDE discretization """
    
    # Compute σ²(ε)
    def sigma_squared_epsilon(epsilon, pre_computed=True):
        """ Compute σ²(ε) = ∫ |y|≤ε y² k(y) dy """
        if pre_computed:
            term1 =  (-(lambda_p * epsilon)**(1 - Y)) * np.exp(-lambda_p * epsilon)
            term2 = (1 - Y) * (g1(0) - g1(lambda_p * epsilon))
            
            term3 =  (-(lambda_n * epsilon)**(1 - Y)) * np.exp(-lambda_n * epsilon)
            term4 = (1 - Y) * (g1(0) - g1(lambda_n * epsilon))

            sigma2_eps = (1 / nu) * lambda_p**(Y - 2) * (term1 + term2) + (1 / nu) * lambda_n**(Y - 2) * (term3 + term4)
            # print(f"sigma2_eps: {sigma2_eps}, term1: {term1}, term2: {term2}, term3: {term3}, term4: {term4}")
            return sigma2_eps
        else:
            y_vals = np.linspace(-epsilon, epsilon, 1000)  
            integral_values = y_vals**2 * k_y(y_vals, lambda_n, lambda_p, nu, Y)
            return np.trapz(integral_values, y_vals)


    # Compute ω(ε)
    def omega_epsilon(epsilon, pre_computed=True):
        """ Compute ω(ε) = ∫ |y|>ε (1 - e^y) k(y) dy """
        if pre_computed:
            term1 = (lambda_p**Y / nu) * g2(lambda_p * epsilon)
            term2 = ((lambda_p - 1)**Y / nu) * g2((lambda_p - 1) * epsilon)
            term3 = (lambda_n**Y / nu) * g2(lambda_n * epsilon)
            term4 = ((lambda_n + 1)**Y / nu) * g2((lambda_n + 1) * epsilon)

            omega_eps = term1 - term2 + term3 - term4
            # print(f"omega_eps: {omega_eps}, term1: {term1}, term2: {term2}, term3: {term3}, term4: {term4}")
            return omega_eps
        else:
            y_vals = np.linspace(epsilon, 10 * epsilon, 1000)  # Approximate upper bound
            integral_values = (1 - np.exp(y_vals)) * k_y(y_vals, lambda_n, lambda_p, nu, Y)
            return np.trapz(integral_values, y_vals)

    # Compute σ²(ε) and ω(ε) once
    sigma2_eps = sigma_squared_epsilon(dx)
    omega_eps = omega_epsilon(dx)

    # Compute B_l and B_u
    B_l = (sigma2_eps * dt) / (2 * dx**2) - ((r - q + omega_eps - 0.5 * sigma2_eps) * (dt / (2 * dx)))
    B_u = (sigma2_eps * dt) / (2 * dx**2) + ((r - q + omega_eps - 0.5 * sigma2_eps) * (dt / (2 * dx)))

    return B_l, B_u

# B_l, B_u = compute_B_coefficients(dx, dt, lambda_n, lambda_p, nu, Y, r, q, pre_computed=True)
# print("Pre-computed :")
# print("B_l =", B_l)
# print("B_u =", B_u)

# B_l, B_u = compute_B_coefficients(dx, dt, lambda_n, lambda_p, nu, Y, r, q, pre_computed=False)
# print("Computed :")
# print("B_l =", B_l)
# print("B_u =", B_u)

In [ ]:
import numpy as np
import scipy.integrate as integrate

# Compute the integral term FOR A CALL ∫_{|y| > Δx} (w(xi + y, τj) − wi,j)k(y)dy
# --> won't be used in the final implementation since we have a direct Rij computation... oh well
def compute_large_jump_integral(w, x_grid, K, N, i, j, dx, nu, lambda_p, lambda_n, Y, g1_n, g1_p, g2_n, g2_p, g2_n_shifted, g2_p_shifted):
    """ Compute the jump integral over |y| > Δx by breaking it into four sub-intervals """
    def integral_1():
        """ Integral over (-∞, x_0 - x_i) """
        return 0 #(lambda_n**Y) * (- w[i, j]) * g2_n(i-1) # would be for the put
    
    def integral_2():
        """ Integral over (x_0 - x_i, -Δx) """
        return sum([
            (lambda_n**Y) * (w[i-k, j] - w[i, j] - k*(w[i-k-1,j] - w[i-k,j])) * (g2_n[k-1] - g2_n[k]) + 
            (w[i-k-1, j] - w[i-k, j]) / (nu * lambda_n**(1-Y) * dx) * (g1_n[k-1] - g1_n[k])
            for k in range(1, i)
        ])
    
    def integral_3():
        """ Integral over (+Δx, x_N - x_i) """
        return sum([
            (lambda_p**Y) * (w[i+k, j] - w[i, j] - k*(w[i+k+1,j] - w[i+k,j])) * (g2_p[k-1] - g2_p[k]) + 
            (w[i+k+1, j] - w[i+k, j]) / (nu * lambda_p**(1-Y) * dx) * (g1_p[k-1] - g1_p[k]) 
            for k in range(1, N-i-1)
        ])
    
    def integral_4():
        """ Integral over (x_N - x_i, ∞) """
        return (((lambda_p-1)**Y) * np.exp(x_grid[i]) * g2_p_shifted[N-i-1]) - ((lambda_p**Y)) * K * g2_p[N-i-1]
    
    return integral_1() + integral_2() + integral_3() + integral_4()

In [ ]:
# Function to compute l, d, u coefficients and R term
def compute_coefficients_put(w, x_grid, N, K, i, j, dx, dt, B_l, B_u, lambda_n, lambda_p, Y, r, nu, precomputed_g_values=None):
    """ Compute coefficients l, d, u and R term for the PIDE discretization """
    if precomputed_g_values:
        # Extract precomputed g1 and g2 values
        g1_n = precomputed_g_values["g1_n"]
        g1_p = precomputed_g_values["g1_p"]
        g2_n = precomputed_g_values["g2_n"]
        g2_p = precomputed_g_values["g2_p"]
        g2_n_shifted = precomputed_g_values["g2_n_shifted"]
        g2_p_shifted = precomputed_g_values["g2_p_shifted"]
    else:
        # Compute g1 and g2 values dynamically
        g1_n = np.array([g1(k * lambda_n * dx) for k in range(1, N)])
        g1_p = np.array([g1(k * lambda_p * dx) for k in range(1, N)])
        g2_n = np.array([g2(k * lambda_n * dx) for k in range(1, N)])
        g2_p = np.array([g2(k * lambda_p * dx) for k in range(1, N)])
        g2_n_shifted = np.array([g2(k * (lambda_n + 1) * dx) for k in range(1, N)])
        g2_p_shifted = np.array([g2(k * (lambda_p - 1) * dx) for k in range(1, N)])

    # Compute l, d, u coefficients
    l_ij1 = -B_l
    d_ij1 = 1 + r * dt + B_l + B_u + (dt / nu) * (
        lambda_n**Y * g2_n[i-1] + lambda_p**Y * g2_p[N - i - 1]
    )
    u_ij1 = -B_u

    # Compute R_i,j
    R_ij = 0
    for k in range(1, i):
        R_ij += lambda_n**Y * (w[i-k, j] - w[i, j] - k * (w[i-k-1, j] - w[i-k, j])) * (g2_n[k-1] - g2_n[k])
        R_ij += (w[i-k-1, j] - w[i-k, j]) / (lambda_n**(1-Y) * dx) * (g1_n[k-1] - g1_n[k])

    for k in range(1, N-i-1): 
        R_ij += lambda_p**Y * (w[i+k, j] - w[i, j] - k * (w[i+k+1, j] - w[i+k, j])) * (g2_p[k-1] - g2_p[k])
        R_ij += (w[i+k+1, j] - w[i+k, j]) / (lambda_p**(1-Y) * dx) * (g1_p[k-1] - g1_p[k])

    R_ij += K * lambda_n**Y * g2_n[i-1] - np.exp(x_grid[i]) * (lambda_n + 1)**Y * g2_n_shifted[i-1]

    return l_ij1, d_ij1, u_ij1, R_ij

# w = np.zeros((N, M))
# w[:, 0] = np.maximum(np.exp(x_grid) - K, 0)
# for j in range(1, M):
#     w[:, j] = w[:, 0]

# i = N // 2  # e.g., middle index
# j = 0       # first time step

# # Test using precomputed g-values
# l_ij1_pre, d_ij1_pre, u_ij1_pre, R_ij_pre = compute_coefficients(
#     w, x_grid, N, K, i, j, dx, dt, B_l, B_u, lambda_n, lambda_p, Y, r, nu, precomputed_g_values
# )
# print("Pre-computed:")
# print("l_ij1, d_ij1, u_ij1, R_ij =", l_ij1_pre, d_ij1_pre, u_ij1_pre, R_ij_pre)

# # Test using dynamic (computed) g-values
# l_ij1_dyn, d_ij1_dyn, u_ij1_dyn, R_ij_dyn = compute_coefficients(
#     w, x_grid, N, K, i, j, dx, dt, B_l, B_u, lambda_n, lambda_p, Y, r, nu, precomputed_g_values=None
# )
# print("Computed:")
# print("l_ij1, d_ij1, u_ij1, R_ij =", l_ij1_dyn, d_ij1_dyn, u_ij1_dyn, R_ij_dyn)

In [18]:
# Function to compute l, d, u coefficients and R term
def compute_coefficients_call(w, x_grid, N, K, i, j, dx, dt, B_l, B_u, lambda_n, lambda_p, Y, r, nu, precomputed_g_values=None):
    """ Compute coefficients l, d, u and R term for the PIDE discretization """
    if precomputed_g_values is None:
        raise ValueError("Precomputed g1 and g2 values must be provided. Recomputing them is not allowed for efficiency reasons.")

    # Extract precomputed g1 and g2 values
    g1_n = precomputed_g_values.get("g1_n")
    g1_p = precomputed_g_values.get("g1_p")
    g2_n = precomputed_g_values.get("g2_n")
    g2_p = precomputed_g_values.get("g2_p")
    g2_n_shifted = precomputed_g_values.get("g2_n_shifted")
    g2_p_shifted = precomputed_g_values.get("g2_p_shifted")
    
    # Ensure all required keys exist in precomputed_g_values
    missing_keys = [key for key in ["g1_n", "g1_p", "g2_n", "g2_p", "g2_n_shifted", "g2_p_shifted"] if key not in precomputed_g_values]
    if missing_keys:
        raise ValueError(f"Missing precomputed g-values: {', '.join(missing_keys)}")

    # Compute l, d, u coefficients
    l_ij1 = -B_l
    d_ij1 = 1 + r * dt + B_l + B_u + (dt/nu) * (lambda_n**Y * g2_n[i-1] + lambda_p**Y * g2_p[N - i - 1])
    u_ij1 = -B_u

    # Compute R_i,j
    jump_integral = compute_large_jump_integral(w, x_grid, K, N, i, j, dx, nu, lambda_p, lambda_n, Y, g1_n, g1_p, g2_n, g2_p, g2_n_shifted, g2_p_shifted)
    R_ij = jump_integral
    
    return l_ij1, d_ij1, u_ij1, R_ij

# w = np.zeros((N, M))
# w[:, 0] = np.maximum(np.exp(x_grid) - K, 0)
# for j in range(1, M):
#     w[:, j] = w[:, 0]

# i = N // 2  # e.g., middle index
# j = 0       # first time step

# # Test using precomputed g-values
# l_ij1_pre, d_ij1_pre, u_ij1_pre, R_ij_pre = compute_coefficients_call(w, x_grid, N, K, i, j, dx, dt, B_l, B_u, lambda_n, lambda_p, Y, r, nu, precomputed_g_values)
# print("Pre-computed:")
# print("l_ij1, d_ij1, u_ij1, R_ij =", l_ij1_pre, d_ij1_pre, u_ij1_pre, R_ij_pre)

# # Test using dynamic (computed) g-values
# l_ij1_dyn, d_ij1_dyn, u_ij1_dyn, R_ij_dyn = compute_coefficients_call(w, x_grid, N, K, i, j, dx, dt, B_l, B_u, lambda_n, lambda_p, Y, r, nu, precomputed_g_values=None)
# print("Computed:")
# print("l_ij1, d_ij1, u_ij1, R_ij =", l_ij1_dyn, d_ij1_dyn, u_ij1_dyn, R_ij_dyn)

In [19]:
# Compute boundary conditions
def apply_boundary_conditions(N, h, I, d, u, w):
    """ Adjust for boundary conditions """
    w[0, :] = (2 / (1 + h/2)) * w[1, :] - (h/2 / (1 + h/2)) * w[2, :]
    w[-1, :] = (- (1 + h/2) / (1 - h/2)) * w[-2, :] + (2 / (1 - h/2)) * w[-3, :]
    return w

In [ ]:
def thomas_algorithm(A, b):
    """Source for this algorithm : stack overflow"""
    N = len(b)
    
    # Extract diagonals from A and create copies
    lower_diag = np.copy(np.diag(A, k=-1))  # l_i (sub-diagonal)
    main_diag = np.copy(np.diag(A, k=0))    # d_i (main diagonal)
    upper_diag = np.copy(np.diag(A, k=1))    # u_i (super-diagonal)

    # Make a copy of b to avoid modifying the input
    b = np.copy(b)

    # Forward elimination
    for i in range(1, N):
        factor = lower_diag[i - 1] / main_diag[i - 1]
        main_diag[i] -= factor * upper_diag[i - 1]
        b[i] -= factor * b[i - 1]

    # Back substitution
    w = np.zeros(N)
    w[-1] = b[-1] / main_diag[-1]
    for i in range(N - 2, -1, -1):
        w[i] = (b[i] - upper_diag[i] * w[i + 1]) / main_diag[i]

    return w

In [ ]:
def iterative_solver(A, b, tol=1e-6, max_iter=1000):
    N = len(b)
    w = np.zeros(N)  # Initial guess (zeros)
    
    for _ in range(max_iter):
        w_old = w.copy()
        
        # Gauss-Seidel iteration
        for i in range(N):
            sum_lower = sum(A[i, j] * w[j] for j in range(i))  # Lower triangular part
            sum_upper = sum(A[i, j] * w_old[j] for j in range(i + 1, N))  # Upper part
            
            w[i] = (b[i] - sum_lower - sum_upper) / A[i, i]
        
        # Check for convergence
        if np.linalg.norm(w - w_old, ord=np.inf) < tol:
            break

    return w

In [22]:
def solve_uoc_pide(x_grid, S0, r, q, Y, K, N, M, dx, dt, nu, lambda_p, lambda_n, method="LU", pre_computed=True, precomputed_g_values=None):
    """
    Solves the UOC option pricing PIDE using an explicit–implicit finite difference scheme.
    
    The PIDE is discretized as:
        l_{i,j+1} * w_{i-1,j+1} + d_{i,j+1} * w_{i,j+1} + u_{i,j+1} * w_{i+1,j+1} 
            = w_{i,j} + (dt/nu) * R_{i,j},
    for interior nodes, while the boundary conditions w(x0, tau)=0 and w(xN, tau)=0 are imposed.
    
    Parameters:
        method (str): "LU", "Thomas", or "Iterative" for solving the linear system.
        
    Returns:
        float: The computed option price at S0 (i.e. at x0 = ln(S0)).
    """
    # Initialize solution matrix w(x, tau) with shape (N, M)
    w = np.zeros((N, M))
    
    # Set initial condition: w(x, 0) = (exp(x) - K)^+ for a call option.
    w[:, 0] = np.maximum(np.exp(x_grid) - K, 0)
    
    # Impose boundary conditions for all time levels (optional since they are re-imposed in the loop)
    w = apply_boundary_conditions(N, dx, 0, 0, 0, w)
    # w[0, :] = 0     # left boundary: x = x_min
    # w[-1, :] = 0    # right boundary: x = x_max (barrier)
    
    # Compute B_l and B_u coefficients
    B_l, B_u = compute_B_coefficients(dx, dt, lambda_n, lambda_p, nu, Y, r, q, pre_computed=True)
    # print(f"B_l: {B_l}, B_u: {B_u}")
    
    # Preallocate matrix A and vector b (of size N, corresponding to the full grid)
    A = np.zeros((N, N))
    b = np.zeros(N)
    
    # Time-marching backward: from j = M-1 down to j = 1.
    for j in range(M - 1, 0, -1):
        # Reset A and b for current time step
        A.fill(0)
        b.fill(0)
        R = np.zeros(N)
        
        # For interior nodes i = 1,..., N-2, compute coefficients and build A and R.
        for i in range(1, N - 1):
            # At point x_i, t_{j+1}
            l_i, d_i, u_i, R[i] = compute_coefficients_call(w, x_grid, N, K, i, j, dx, dt, B_l, B_u, lambda_n, lambda_p, Y, r, nu, precomputed_g_values)
            A[i, i - 1] = l_i
            A[i, i]     = d_i
            A[i, i + 1] = u_i
            # print(f"{i},{j} : l_i: {l_i}, d_i: {d_i}, u_i: {u_i}, R_i: {R[i]}")
        
        # Enforce boundary conditions in the linear system:
        # For the left boundary (i=0) and right boundary (i=N-1), we want w=0.
        A[0, :] = 0
        A[0, 0] = 1 # prevents non invertible 
        b[0] = 0
        
        A[-1, :] = 0
        A[-1, -1] = 1
        b[-1] = 0
        
        # print("R = ", R)
        
        # Build right-hand side for interior nodes:
        b[1:-1] = w[1:-1, j] + (dt / nu) * R[1:-1]
        
        # Solve the linear system A * sol = b using the chosen method.
        if method == "LU":
            L, U = la.lu(A, permute_l=True)
            sol = la.solve(U, la.solve(L, b))
        elif method == "Thomas":
            sol = thomas_algorithm(A, b)
        elif method == "Iterative":
            sol = iterative_solver(A, b)
        elif method == "scipy":
            sol = la.solve(A, b)
        else:
            raise ValueError("Invalid method. Choose from 'LU', 'Thomas', or 'Iterative'.")
        
        # Update solution at time step j-1 with the computed solution.
        w[:, j - 1] = sol
        
        # Re-impose the boundary conditions explicitly.
        w[0, j - 1] = 0
        w[-1, j - 1] = 0

    # Find the index corresponding to x0 = ln(S0)
    x0_index = np.argmin(np.abs(x_grid - np.log(S0)))
    
    # Return the option price at the node closest to S0
    # print("w =", w)
    return w[x0_index, 0]


---

## First run for given and intuited values 

In [23]:
# Parameters
S0 = 1900  # Spot price
K = 2000  # Strike price
B = 2200  # Barrier
r = 0.0025  # Risk-free rate 
q = 0.015  # Dividend rate
T = 0.5  # Maturity
sigma = 0.25  # Volatility
nu = 0.31  # Jump intensity
theta = -0.25  # Mean jump size
Y = 0.4  # Tail index

# Grid parameters
N = 100  # Number of spatial steps
total_points = N + 1
M = 100  # Number of time steps

# Define the spatial grid range in log-space
# -1.5, -1.0, -0.5, 0, 0.5, 1.0, 1.5
x_min = np.log(S0) - 1.5 # Lower bound in log-space
x_max = np.log(B)  # Upper bound (log barrier level)

# D = 
# x_i = x_min + i * dx, i = 0, 1, ..., N
# t_j = 0 + j * dt, j = 0, 1, ..., M
dx = (x_max - x_min) / (N-1)  # Spatial step size
dt = T / (M-1)  # Time step size

# Discretized spatial and time grids
x_grid = np.linspace(x_min, x_max, N)
tau_grid = np.linspace(0, T, M)

# Display the computed grid parameters
grid_params = {
    "x_min": x_min,
    "x_max": x_max,
    "dx": dx,
    "dt": dt,
    "Number of spatial points": N,
    "Number of time points": M,
}

grid_params

{'x_min': 6.049609165154532,
 'x_max': 7.696212639346407,
 'dx': 0.016632358325170453,
 'dt': 0.005050505050505051,
 'Number of spatial points': 100,
 'Number of time points': 100}

In [24]:
# Compute lambda parameters
lambda_p = ((theta**2 / sigma**4) + (2 / (sigma**2 * nu)))**(1/2) - (theta / sigma**2)
lambda_n = ((theta**2 / sigma**4) + (2 / (sigma**2 * nu)))**(1/2) + (theta / sigma**2)

print("lambda_p =", lambda_p, "lambda_n =", lambda_n)

lambda_p = 14.919057031246467 lambda_n = 6.919057031246467


In [25]:
# Precompute g1 and g2 values for efficiency
precomputed_g_values = {
    "g1_n": np.array([g1(k * lambda_n * dx) for k in range(1, N+1)]),
    "g1_p": np.array([g1(k * lambda_p * dx) for k in range(1, N+1)]),
    "g2_n": np.array([g2(k * lambda_n * dx) for k in range(1, N+1)]),
    "g2_p": np.array([g2(k * lambda_p * dx) for k in range(1, N+1)]),
    "g2_n_shifted": np.array([g2(k * (lambda_n + 1) * dx) for k in range(1, N+1)]),
    "g2_p_shifted": np.array([g2(k * (lambda_p - 1) * dx) for k in range(1, N+1)])
}

In [26]:
# Choose the solver method: "LU", "Thomas", or "Iterative"
solver_method = "scipy"  # Change this to "LU" or "Iterative" if needed

# Compute the option price using the chosen method
option_price = solve_uoc_pide(x_grid, S0, r, q, Y, K, N, M, dx, dt, nu, lambda_p, lambda_n, method=solver_method, pre_computed=True, precomputed_g_values=precomputed_g_values)

# Print the computed option price
print(f"Computed Up-and-Out Call Option Price using {solver_method} method: {option_price:.4f}")

Computed Up-and-Out Call Option Price using scipy method: 17.3199


---

## Testing Stability and Convergence

In [ ]:
import numpy as np
import scipy.linalg as la
import scipy.integrate as spi
import itertools
import pandas as pd

# Define grid setup function:
def setup_grid(delta, N, M):
    x_min = np.log(K) - delta
    x_max = np.log(B)
    dx = (x_max - x_min) / (N-1)
    dt = T / (M-1)
    x_grid = np.linspace(x_min, x_max, N)
    tau_grid = np.linspace(0, T, M)
    grid_params = {"x_min": x_min, "x_max": x_max, "dx": dx, "dt": dt, "N": N, "M": M}
    return grid_params, x_grid, dx, dt


# Precompute g-values for given dx and N:
def compute_precomputed_g(dx, N):
    precomputed_g_values = {
        "g1_n": np.array([g1(k * lambda_n * dx) for k in range(1, N)]),
        "g1_p": np.array([g1(k * lambda_p * dx) for k in range(1, N)]),
        "g2_n": np.array([g2(k * lambda_n * dx) for k in range(1, N)]),
        "g2_p": np.array([g2(k * lambda_p * dx) for k in range(1, N)]),
        "g2_n_shifted": np.array([g2(k * (lambda_n + 1) * dx) for k in range(1, N)]),
        "g2_p_shifted": np.array([g2(k * (lambda_p - 1) * dx) for k in range(1, N)])
    }
    return precomputed_g_values


# Sensitivity analysis over delta, N, M:
delta_values = [0.1, 0.2, 0.3, 0.5, 0.75, 1.0, 1.5]  # for x_min = ln(K) - delta
N_values = [50, 75, 100, 150, 200, 250]            # spatial steps
M_values = [50, 75, 100, 150, 200, 250]            # time steps

results = []
for delta, N_val, M_val in itertools.product(delta_values, N_values, M_values):
    grid_params, x_grid, dx, dt = setup_grid(delta, N_val, M_val)
    precomputed_g = compute_precomputed_g(dx, N_val)
    # Use N_val and M_val in the solver call (not global N, M)
    option_price = solve_uoc_pide(x_grid, S0, r, q, Y, K, N_val, M_val, dx, dt, nu, lambda_p, lambda_n, 
                                  method="scipy", pre_computed=True, precomputed_g_values=precomputed_g)
    results.append({
        "delta": delta,
        "N": N_val,
        "M": M_val,
        "OptionPrice": option_price
    })

df = pd.DataFrame(results)
print(df)

# Save the DataFrame to a pickle file for later use
df.to_pickle('results_df.pkl')

In [ ]:
import pandas as pd

df = pd.read_pickle('results_df.pkl')
df.to_csv('results_df.csv', index=False)
# data = df[df["OptionPrice"]>=15]

In [ ]:
import numpy as np
import pandas as pd
from scipy.interpolate import griddata
import plotly.graph_objs as go

df = pd.read_pickle('results_df.pkl')
# df = df[df["OptionPrice"]>=15]

# Create a dense regular grid for interpolation
N_lin = np.linspace(df['N'].min(), df['N'].max(), 50)
M_lin = np.linspace(df['M'].min(), df['M'].max(), 50)
delta_lin = np.linspace(df['delta'].min(), df['delta'].max(), 50)
N_grid, M_grid, delta_grid = np.meshgrid(N_lin, M_lin, delta_lin, indexing='ij')

# Prepare the original points and values
points = df[['N', 'M', 'delta']].values  # shape: (n_points, 3)
values = df['OptionPrice'].values

# Interpolate onto the dense grid
grid_points = np.column_stack((N_grid.ravel(), M_grid.ravel(), delta_grid.ravel()))
grid_option_price = griddata(points, values, grid_points, method='linear')

# Reshape interpolated values back to the grid shape
grid_option_price = grid_option_price.reshape(N_grid.shape)

# Create a continuous volume plot using Plotly
fig = go.Figure(data=go.Volume(
    x=N_grid.flatten(),
    y=M_grid.flatten(),
    z=delta_grid.flatten(),
    value=grid_option_price.flatten(),
    isomin=np.nanmin(grid_option_price),
    isomax=np.nanmax(grid_option_price),
    opacity=0.1,         # Adjust for your desired visibility
    surface_count=100,    # Increase for more isosurfaces
    colorscale='Jet',    # Choose any colorscale you prefer
    colorbar=dict(title='Option Price')
))

# Customize the layout
fig.update_layout(
    title='Continuous 4D Visualization of Option Price',
    scene=dict(
        xaxis_title='N (Spatial Steps)',
        yaxis_title='M (Time Steps)',
        zaxis_title='Delta'
    )
)

fig.show()


---
# Conclusion

## Summary of Implementation

This homework implemented a **finite difference method (FDM) with jump processes** to price **up-and-out call (UOC) options** under a jump-diffusion model. The Partial Integro-Differential Equation (PIDE) governing the option price was discretized using a **semi-implicit scheme**, accounting for the jump integral through **precomputed numerical quadrature functions** $ g_1 $ and $ g_2 $ (given in class).

The **Thomas algorithm**, **LU decomposition**, and **iterative solvers** were implemented to efficiently solve the resulting tridiagonal system at each time step. The solution was computed for varying grid resolutions to analyze **numerical stability and convergence**.

---

## Observations on the Results

- The option price **converges** as the number of spatial ($ N $) and time ($ M $) steps increases.
- **Higher grid resolutions** ($ N, M \to \infty $) produce more stable prices, confirming the accuracy of the discretization.
- The price is sensitive to **$ \delta $** (the spatial domain extension), affecting stability:
  - Smaller $ \delta $ leads to more accurate boundary approximations.
  - Larger $ \delta $ includes more price dynamics but slows convergence.
- The jump parameters $ \lambda_n $ and $ \lambda_p $ significantly influence price behavior.

---

## Stability and Convergence

- **Consistency**: The method remains **first-order accurate** in time and **second-order accurate** in space.
- **Stability**: The scheme is conditionally stable, as shown by smooth price evolution for increasing $ N, M $.
- **Convergence**: The solution converges to a stable price as the mesh is refined.

### Trade-offs in Grid Selection:
- **Small $ N, M $** → faster computation but less accuracy.
- **Large $ N, M $** → higher accuracy but increased computation time.
- **Precomputed integrals** ($ g_1, g_2 $) significantly improve speed (as I realized a bit too late in my experience...).

---

## Future Improvements

- **Adaptive Grids**: Refining the mesh adaptively near **critical regions (barrier, strike price)** could enhance accuracy while reducing computational cost, as we saw in class.
- **Higher-Order Schemes**: Using **Crank-Nicolson** or **Runge-Kutta discretizations** could improve stability and reduce time step sensitivity, like we did see in class as well.
- **Parallelization**: Implementing the jump integral computation in **vectorized form (NumPy, GPU acceleration)** can further speed up execution - this could be very efficient but I feel like this wasn't what as tasked here.

---

## Final Thoughts

This homework implementation shows the effectiveness of **PIDE discretization** for exotic option pricing under **jump-diffusion models**. The results confirm **numerical convergence**, and the methodology is applicable to other **Lévy-driven financial models** !! :) <br>
(we'd have to use analytical way of computing omega_epsilon, sigma_squared_epsilon instead of the direct expression we derived)